# Classification k-NN Corse - Version ipyleaflet

Cette version utilise **ipyleaflet** avec des interactions Python natives (pas de JavaScript injecté).

**Avantage :** Fonctionne parfaitement dans Jupyter sans problème d'iframe ou de JavaScript.

In [ ]:
# Installation
!pip install ipyleaflet ipywidgets pandas numpy scikit-learn --quiet

In [ ]:
import pandas as pd
import numpy as np
from ipyleaflet import Map, CircleMarker, Marker, Polyline, LayerGroup, WidgetControl, AwesomeIcon
from ipywidgets import HTML, VBox, HBox, Label, IntSlider, Output
from sklearn.neighbors import KNeighborsClassifier
from IPython.display import display


## 1. Chargement des données

In [ ]:
# Chargement
df_coords = pd.read_csv('communes-de-corse-en-corse-et-francais.csv', sep=';', encoding='utf-8')
df_territoires = pd.read_csv('communes-par-territoire-de-projet-de-la-collectivite-territoriale-de-corse0.csv', 
                             sep=';', encoding='utf-8')

print(f"✅ {len(df_coords)} communes avec coordonnées")
print(f"✅ {len(df_territoires)} communes avec territoires")

In [ ]:
# Extraction coordonnées
def extract_coordinates(point_geo_str):
    if pd.isna(point_geo_str):
        return None, None
    try:
        coords = str(point_geo_str).strip().split(',')
        if len(coords) == 2:
            return float(coords[0].strip()), float(coords[1].strip())
    except:
        pass
    return None, None

df_coords[['Latitude', 'Longitude']] = df_coords['Point_Geo'].apply(
    lambda x: pd.Series(extract_coordinates(x))
)

print(f"✅ {df_coords['Latitude'].notna().sum()} coordonnées extraites")

In [ ]:
# Fusion
def normalize(name):
    return str(name).upper().strip() if not pd.isna(name) else ''

df_coords['Commune_norm'] = df_coords['Nom français'].apply(normalize)
df_territoires['Commune_norm'] = df_territoires['Commune'].apply(normalize)

df = pd.merge(df_coords, df_territoires[['Commune_norm', 'Territoire de projet']], 
              on='Commune_norm', how='inner')
df['Commune'] = df['Nom français']
df_clean = df.dropna(subset=['Latitude', 'Longitude', 'Territoire de projet']).copy()

print(f"✅ {len(df_clean)} communes fusionnées")
print(f"\nMicro-régions: {len(df_clean['Territoire de projet'].unique())}")
for region in sorted(df_clean['Territoire de projet'].unique()):
    count = (df_clean['Territoire de projet'] == region).sum()
    print(f"  • {region}: {count} communes")

## 2. Entraînement k-NN

In [ ]:
# Modèle k-NN
X = df_clean[['Latitude', 'Longitude']].values
y = df_clean['Territoire de projet'].values

knn = KNeighborsClassifier(n_neighbors=5, weights='distance', metric='haversine')
X_rad = np.radians(X)
knn.fit(X_rad, y)

print(f"✅ Modèle k-NN entraîné")
print(f"✅ {len(df_clean)} communes")
print(f"✅ {len(np.unique(y))} micro-régions")

## 3. Configuration des couleurs

In [ ]:
# Couleurs par micro-région
microregions = sorted(df_clean['Territoire de projet'].unique())
colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred', 
          'lightcoral', 'beige', 'darkblue', 'darkgreen', 'cadetblue', 
          'darkviolet', 'pink', 'lightblue', 'lightgreen', 'gray']

color_map = {region: colors[i % len(colors)] for i, region in enumerate(microregions)}

print("✅ Couleurs configurées:")
for region, color in sorted(color_map.items()):
    print(f"  • {region}: {color}")

## 4. Création de la carte interactive

In [ ]:
# Carte ipyleaflet
center_lat = df_clean['Latitude'].mean()
center_lon = df_clean['Longitude'].mean()

m = Map(
    center=(center_lat, center_lon),
    zoom=9,
    scroll_wheel_zoom=True
)

# Ajouter les communes
commune_layer = LayerGroup(name='Communes')

for idx, row in df_clean.iterrows():
    marker = CircleMarker(
        location=(row['Latitude'], row['Longitude']),
        radius=3,
        color=color_map[row['Territoire de projet']],
        fill_color=color_map[row['Territoire de projet']],
        fill_opacity=0.7,
        weight=1
    )
    # Popup avec info
    marker.popup = HTML(f"<b>{row['Commune']}</b><br>{row['Territoire de projet']}")
    commune_layer.add_layer(marker)

m.add_layer(commune_layer)

print(f"✅ {len(df_clean)} communes ajoutées à la carte")

## 5. Interface interactive avec widgets

In [ ]:
# Widgets
k_slider = IntSlider(
    value=5,
    min=1,
    max=15,
    step=1,
    description='k voisins:',
    continuous_update=False
)

info_html = HTML(
    value="<div style='background:#e3f2fd;padding:10px;border-radius:5px;'>"
          "<b>🖱️ Cliquez sur la carte</b> pour prédire la micro-région.<br>"
          "Ajustez <b>k</b> pour changer le nombre de voisins."
          "</div>"
)

result_output = Output()

# Stocker les coordonnées courantes
current_coords = {'lat': None, 'lon': None}

# Layer pour la prédiction
prediction_layer = LayerGroup(name='Prédiction')
m.add_layer(prediction_layer)

print("✅ Widgets créés")

In [ ]:
# Fonction de prédiction
def update_classification(lat, lon, k_value):
    """Met à jour la classification pour un point donné."""
    # Prédiction
    coords_rad = np.radians([[lat, lon]])
    knn.n_neighbors = k_value
    knn.fit(X_rad, y)  # Réentraîner avec nouveau k
    predicted_region = knn.predict(coords_rad)[0]
    
    # Trouver les k plus proches voisins
    distances, indices = knn.kneighbors(coords_rad)
    distances_km = distances[0] * 6371  # Conversion en km
    
    # Nettoyer la couche de prédiction
    prediction_layer.clear_layers()
    
    # Créer une icône personnalisée avec AwesomeIcon
    custom_icon = AwesomeIcon(
        name='star',
        marker_color=color_map[predicted_region],
        icon_color='white',
        spin=False
    )
    
    # Ajouter le marqueur de prédiction
    prediction_marker = Marker(
        location=(lat, lon),
        draggable=False,
        icon=custom_icon
    )
    
    # Popup détaillé
    popup_html = f"""<div style='min-width:220px;'>
        <h4 style='margin:5px 0;color:{color_map[predicted_region]};'>🎯 {predicted_region}</h4>
        <p style='margin:5px 0;font-size:11px;'>
            <b>Coordonnées:</b><br>
            Lat: {lat:.5f}°<br>
            Lon: {lon:.5f}°
        </p>
        <hr style='margin:5px 0;'>
        <p style='margin:5px 0;font-size:11px;'><b>{k_value} plus proches communes:</b></p>
        <ul style='margin:5px 0;padding-left:20px;font-size:10px;'>"""
    
    for i, idx in enumerate(indices[0]):
        commune_info = df_clean.iloc[idx]
        popup_html += f"<li><b>{commune_info['Commune']}</b> ({distances_km[i]:.2f} km)</li>"
    
    popup_html += "</ul></div>"
    prediction_marker.popup = HTML(popup_html)
    prediction_layer.add_layer(prediction_marker)
    
    # Ajouter les lignes vers les k plus proches voisins
    for i, idx in enumerate(indices[0]):
        commune_info = df_clean.iloc[idx]
        line = Polyline(
            locations=[
                (lat, lon),
                (commune_info['Latitude'], commune_info['Longitude'])
            ],
            color='gray',
            weight=2,
            opacity=0.6,
            dash_array='8, 8'
        )
        prediction_layer.add_layer(line)
    
    # Afficher le résultat
    with result_output:
        result_output.clear_output()
        print(f"\n🎯 Prédiction: {predicted_region}")
        print(f"📍 Coordonnées: ({lat:.5f}, {lon:.5f})")
        print(f"\n{k_value} plus proches communes:")
        for i, idx in enumerate(indices[0]):
            commune_info = df_clean.iloc[idx]
            print(f"  {i+1}. {commune_info['Commune']:30s} - {distances_km[i]:6.2f} km")

print("✅ Fonction de prédiction définie")


In [ ]:
# Gestionnaires d'événements
def handle_click(**kwargs):
    """Gestionnaire de clic sur la carte."""
    if kwargs.get('type') == 'click':
        coords = kwargs.get('coordinates')
        lat, lon = coords
        current_coords['lat'] = lat
        current_coords['lon'] = lon
        update_classification(lat, lon, k_slider.value)

def on_k_change(change):
    """Gestionnaire de changement de k."""
    if current_coords['lat'] is not None:
        update_classification(current_coords['lat'], current_coords['lon'], change['new'])

# Connecter les événements
m.on_interaction(handle_click)
k_slider.observe(on_k_change, names='value')

print("✅ Gestionnaires d'événements connectés")

## 6. Affichage de l'interface complète

In [ ]:
# Légende HTML
legend_html = "<div style='background:white;padding:10px;border-radius:5px;max-height:300px;overflow-y:auto;'>"
legend_html += "<h4 style='margin-top:0;'>🗺️ Micro-régions</h4>"
for region, color in sorted(color_map.items()):
    legend_html += f"<div style='margin:3px 0;'><span style='display:inline-block;width:12px;height:12px;background:{color};border-radius:50%;margin-right:5px;'></span>{region}</div>"
legend_html += "</div>"

legend_widget = HTML(legend_html)
legend_control = WidgetControl(widget=legend_widget, position='topright')
m.add_control(legend_control)

# Afficher l'interface complète
display(VBox([
    info_html,
    HBox([Label(''), k_slider]),
    m,
    result_output
]))

print("\n" + "="*60)
print("✅ CARTE INTERACTIVE PRÊTE!")
print("="*60)
print("\n🖱️ Cliquez n'importe où sur la carte pour prédire la micro-région.")
print("🎚️ Utilisez le slider pour changer k (nombre de voisins).")
print("\n⭐ Cette version utilise ipyleaflet avec interactions Python natives.")
print("   Pas de JavaScript injecté = Fonctionne parfaitement dans Jupyter!")

## 7. Fonction de test (optionnel)

In [ ]:
# Test manuel
def test_prediction(lat, lon, k_val=5):
    """Tester une prédiction avec des coordonnées spécifiques."""
    print(f"\nTest de prédiction pour ({lat}, {lon}) avec k={k_val}")
    print("="*60)
    update_classification(lat, lon, k_val)

# Exemples
# test_prediction(42.15, 9.15, 5)  # Centre Corse
# test_prediction(42.55, 8.85, 5)  # Nord
# test_prediction(41.65, 9.15, 5)  # Sud

## Conclusion

✅ **Carte interactive fonctionnelle avec ipyleaflet**

**Avantages par rapport à Folium :**
- ✅ Interactions Python natives (pas de JavaScript injecté)
- ✅ Fonctionne parfaitement dans Jupyter
- ✅ Pas de problème d'iframe ou de sécurité
- ✅ Slider interactif pour changer k en temps réel
- ✅ Résultats affichés sous la carte

**Utilisation :**
1. Cliquez sur la carte → Prédiction s'affiche avec marqueur et lignes
2. Changez k avec le slider → Prédiction se met à jour automatiquement
3. Les résultats détaillés s'affichent sous la carte

**Note :** Cette version ne génère pas de fichier HTML standalone car ipyleaflet nécessite un serveur Jupyter pour les interactions Python. Pour partager, utilisez Jupyter nbviewer ou Binder.